#### This notebook illustrates a 

In [ ]:
import torch
import datasets
from datasets import load_dataset, list_datasets

ri = (datasets.ReadInstruction('train', to=50, unit='%'))#+
train_0_50pct_ds = load_dataset("IWSLT/ted_talks_iwslt", language_pair=("en", "fr"), year="2016", split=ri)
print(train_0_50pct_ds)


: 

In [2]:
ri = (datasets.ReadInstruction('train', from_=95, unit='%')) #
test_95_100pct_ds = load_dataset("IWSLT/ted_talks_iwslt", language_pair=("en", "fr"), year="2016", split=ri)

Using custom data configuration en_fr_2016-11a4e0bc5e5736c0
Reusing dataset ted_talks_iwslt (/home/silvija/.cache/huggingface/datasets/IWSLT___ted_talks_iwslt/en_fr_2016-11a4e0bc5e5736c0/1.1.0/a42f763b98f8e9cc19358a2ac1007b0b600554e260ee48e6316df39703ef37a4)


In [3]:
print(test_95_100pct_ds)

Dataset({
    features: ['translation'],
    num_rows: 204
})


In [4]:
from transformers import T5ForConditionalGeneration, T5Tokenizer
checkpoint = "google-t5/t5-small"
modelname='t5-small'
model = T5ForConditionalGeneration.from_pretrained(modelname)
tokenizer = T5Tokenizer.from_pretrained(modelname)


In [5]:
#hide_output: after running it right-click to clear the cell's output
from tqdm import tqdm
inputs = []
targets=[]
for _, examples in tqdm(zip(range(200), iter(test_95_100pct_ds)), total=200):
    inputs.append(examples["translation"]['en']);
    targets.append(examples["translation"]['fr']);
model_inputs = tokenizer(inputs, text_target=targets, max_length=128, truncation=True);

100%|██████████████████████████████████████████████████████████| 200/200 [00:00<00:00, 29367.76it/s]
Keyword arguments {'text_target': ['Que se passe-t-il quand un noir visite Aspen? L\'auteur-compositeur-interprète Stew est sur le point de vous le faire découvrir, avec l\'humour acide et intelligent qui caractérise son travail. (Indice : "c\'est un pays des merveilles d\'hiver dans l\'antre de la bête"). Stew est accompagné sur scène par Heidi Rodewald à la basse et Jon Spurney au clavier et à la guitare.', 'Stew chante "Black Men Ski" ("Les noirs skient")', "Les fondateurs de Google, Larry Page et Sergey Brin nous offre une immersion dans l'univers Google. Ils partagent des anecdotes sur le modèle de recherche international, la fondation philanthropique Google et la culture Google de recherche perpétuelle d'innovation et de bonheur des employés.", 'Sergey Brin et Larry Page parlent de Google', 'La violoniste Natalie MacMaster et le directeur musical de TED Thomas Dolby jouent la chan

In [ ]:
from tqdm import tqdm

for _, examples in tqdm(zip(range(200), iter(test_95_100pct_ds)), total=200):
    inputs=examples["translation"]['en'];
    targets = examples["translation"]['fr'];
    model_inputs0 = tokenizer(inputs, text_target=targets, max_length=128, truncation=True);

In [12]:
ex=next(iter(test_95_100pct_ds))
ex1=ex['translation']['en']
ex2=ex['translation']['fr']
print(ex1)
print(ex2)

What happens when a black man visits Aspen? Singer/songwriter Stew and his band are about to let you know.
Que se passe-t-il quand un noir visite Aspen? L'auteur-compositeur-interprète Stew est sur le point de vous le faire découvrir, avec l'humour acide et intelligent qui caractérise son travail. (Indice : "c'est un pays des merveilles d'hiver dans l'antre de la bête"). Stew est accompagné sur scène par Heidi Rodewald à la basse et Jon Spurney au clavier et à la guitare.


In [13]:
source_lang = "en"
target_lang = "fr"
prefix = "translate English to French: "
def preprocess_function(examples):
    #inputs = [prefix + example[source_lang] for example in examples["translation"]]
    inputs = [example[source_lang] for example in examples["translation"]];
    targets = [example[target_lang] for example in examples["translation"]];
    model_inputs = tokenizer(inputs, text_target=targets, max_length=128, truncation=True);
    return model_inputs

In [ ]:
%%capture --no-display
tokenized_books = test_95_100pct_ds.map(preprocess_function, batched=True)

In [17]:
model_inputs0

{'input_ids': [901, 1263, 60, 10, 71, 3027, 53, 8, 3298, 5362, 1], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

In [21]:
len(model_inputs['input_ids'][1])

9

In [22]:
tokenized_books

Dataset({
    features: ['attention_mask', 'input_ids', 'translation'],
    num_rows: 204
})

In [23]:
from torch.utils.data import DataLoader

def train_translation_model(model, dataset, optimizer, epochs):
    dataloader = DataLoader(dataset, batch_size=16)
    model.train()
    for epoch in range(epochs):
        for batch in dataloader:
            optimizer.zero_grad()
            outputs = model(input_ids=batch["input_ids"], labels=batch["translation"])
            loss = outputs.loss
            loss.backward()
            optimizer.step()

from nltk.translate.bleu_score import sentence_bleu

def evaluate_bleu(reference, prediction):
    return sentence_bleu([reference.split()], prediction.split())

In [33]:
from torch.optim import AdamW
optimizer = AdamW(model.parameters(), lr=2e-4)
train_translation_model(model, tokenized_books, optimizer, 2)

RuntimeError: each element in list of batch should be of equal size

In [24]:
from torch.utils.data import DataLoader
dataloader = DataLoader(tokenized_books, batch_size=16)

In [25]:
itdata=iter(dataloader)
batch = next(itdata)

RuntimeError: each element in list of batch should be of equal size

In [26]:
from transformers import DataCollatorForSeq2Seq

checkpoint = "google-t5/t5-small"
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=checkpoint)

2024-10-18 16:44:38.729881: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-10-18 16:44:38.748705: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-10-18 16:44:39.213130: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [28]:
import evaluate

metric = evaluate.load("sacrebleu")

ImportError: cannot import name 'DownloadMode' from 'datasets' (/home/silvija/nlp_notebooks/virtualENV/lib/python3.8/site-packages/datasets/__init__.py)

In [29]:
import numpy as np


def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [[label.strip()] for label in labels]

    return preds, labels


def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)

    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)

    result = metric.compute(predictions=decoded_preds, references=decoded_labels)
    result = {"bleu": result["score"]}

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    result = {k: round(v, 4) for k, v in result.items()}
    return result

In [30]:
from transformers import Seq2SeqTrainingArguments, Seq2SeqTrainer
training_args = Seq2SeqTrainingArguments(
    output_dir="my_awesome_opus_books_model",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=2,
    predict_with_generate=True,
    fp16=True, #change to bf16=True for XPU
    push_to_hub=True,
)

trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_books,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

Cloning https://huggingface.co/kokaljfilipovic/my_awesome_opus_books_model into local empty directory.


OSError: WARNING: `git lfs clone` is deprecated and will not be updated
          with new flags from `git clone`

`git clone` has been updated in upstream Git to have comparable
speeds to `git lfs clone`.
Cloning into '.'...
remote: Repository not found
fatal: repository 'https://huggingface.co/kokaljfilipovic/my_awesome_opus_books_model/' not found
Error(s) during clone:
`git clone` failed: exit status 128
